Author: *

Date: 27.11.2017

In [1]:
import netgen.gui
from netgen.geom2d import *
from ngsolve import *
from ngsolve.internal import *
import numpy as np
import time

%gui tk

In [2]:
class MyGeometry:
    def __init__(self, diameter, alpha, verticalDistance, rows, columns, canalWidth, canalLength, radiusI, sourceHeight):
        self.diameter = diameter
        self.alpha = alpha
        self.verticalDistance = verticalDistance
        self.horizontalDistance = 2*verticalDistance*sin(alpha/2)
        self.rows = rows
        self.columns = columns
        self.canalWidth = canalWidth
        self.canalLength = canalLength
        self.radiusI = radiusI
        self.geo = SplineGeometry()
        self.xMid=self.columns*self.horizontalDistance/2.0
        self.sourceHeight = sourceHeight
        self.createRest()
     
    def createMesh(self):                    
        self.geo.SetMaterial (1, "matrix")
        self.geo.SetMaterial (2, "hole")
        self.geo.SetMaterial (3, "entry")
        self.geo.SetMaterial (4, "air")
        self.geo.SetMaterial (5, "plm")
        self.geo.SetMaterial (6, "source")
        self.mesh = Mesh(self.geo.GenerateMesh(maxh=0.08))
        
    def createRest(self):
        xMid=self.columns*self.horizontalDistance/2.0
        width=self.columns*self.horizontalDistance
        height=self.rows*self.verticalDistance
        p1,p2,p3,p4,p5,p6=[self.geo.AppendPoint(x,y) for x,y in [(0,0), (xMid-self.canalWidth/2,0),(xMid+self.canalWidth/2,0), (width,0), (width,height), (0,height)]]
        self.geo.Append (["line", p1, p2], leftdomain=1, rightdomain=0)
        self.geo.Append (["line", p2, p3], leftdomain=1, rightdomain=3)
        self.geo.Append (["line", p3, p4], leftdomain=1, rightdomain=0)
        self.geo.Append (["line", p4, p5], leftdomain=1, rightdomain=4)       
        self.geo.Append (["line", p5, p6], leftdomain=1, rightdomain=4)
        self.geo.Append (["line", p6, p1], leftdomain=1, rightdomain=4)          
        
        p7,p8=[self.geo.AppendPoint(x,y) for x,y in [(xMid-self.canalWidth/2,-self.canalLength),(xMid+self.canalWidth/2,-self.canalLength)]]       
        self.geo.Append (["line", p2, p7], leftdomain=3, rightdomain=0)       
        self.geo.Append (["line", p7, p8], leftdomain=3, rightdomain=6)
        self.geo.Append (["line", p8, p3], leftdomain=3, rightdomain=0)
        
        p19,p20=[self.geo.AppendPoint(x,y) for x,y in [(xMid-self.canalWidth/2,-self.canalLength-self.sourceHeight),(xMid+self.canalWidth/2,-self.canalLength-self.sourceHeight)]]       
        self.geo.Append (["line", p7, p19], leftdomain=6, rightdomain=0)       
        self.geo.Append (["line", p19, p20], leftdomain=6, rightdomain=0)
        self.geo.Append (["line", p20, p8], leftdomain=6, rightdomain=0)        
 
        p9,p10,p11,p12,p13=[self.geo.AppendPoint(x,y) for x,y in [(xMid+self.radiusI,0),(xMid+self.radiusI,self.radiusI),(xMid,self.radiusI),(xMid-self.radiusI,self.radiusI),(xMid-self.radiusI,0)]]       
        self.geo.Append (["line", p4, p9], leftdomain=4, rightdomain=0)       
        self.geo.Append (["spline3", p9, p10, p11], leftdomain=4, rightdomain=5)
        self.geo.Append (["spline3", p11, p12, p13], leftdomain=4, rightdomain=5)        
        self.geo.Append (["line", p13, p1], leftdomain=4, rightdomain=0)
        
        radiusO=self.radiusI*1.2
        p14,p15,p16,p17,p18=[self.geo.AppendPoint(x,y) for x,y in [(xMid+radiusO,0),(xMid+radiusO,radiusO),(xMid,radiusO),(xMid-radiusO,radiusO),(xMid-radiusO,0)]]       
        self.geo.Append (["line", p9, p14], leftdomain=5, rightdomain=0)       
        self.geo.Append (["spline3", p14, p15, p16], leftdomain=5, rightdomain=0)
        self.geo.Append (["spline3", p16, p17, p18], leftdomain=5, rightdomain=0)        
        self.geo.Append (["line", p18, p13], leftdomain=5, rightdomain=0)
        
        
    def createWithoutHoles(self):
        self.createMesh()
        
    def createEquidistantGeometry(self):
        for r in range(self.rows):
            for c in range(self.columns):
                if(r % 2 ==0):
                    xValue = self.horizontalDistance/2+c*self.horizontalDistance
                    yValue = self.verticalDistance/2+r*self.verticalDistance
                    self.geo.AddCircle(c=(xValue,yValue),r=self.diameter/2,bc="circle",leftdomain=2,rightdomain=1)
                elif(c!=self.columns-1):
                    xValue = self.horizontalDistance+c*self.horizontalDistance
                    yValue = self.verticalDistance/2+r*self.verticalDistance
                    self.geo.AddCircle(c=(xValue,yValue),r=self.diameter/2,bc="circle",leftdomain=2,rightdomain=1)
        self.createMesh()

In [3]:
myGeo = MyGeometry(0.02,90,0.02,37,37,0.2,0.5,1.1,0.04)
myGeo.createEquidistantGeometry()

In [4]:
mesh=myGeo.mesh

#Question:
#How to set the ElementOrder to 5?
mesh.SetElementOrder(5)
#
mesh.SetPML(pml.Radial(rad=myGeo.radiusI, alpha=1j, origin=(myGeo.xMid, 0)), "pml")
viewoptions.drawoutline=1
Draw(mesh)

TypeError: SetElementOrder(): incompatible function arguments. The following argument types are supported:
    1. (self: ngsolve.comp.Mesh, arg0: ngsolve.comp.ElementId, arg1: int) -> None

Invoked with: <ngsolve.comp.Mesh object at 0x000001EE83190B48>, 5

In [ ]:
fes = H1(mesh, order = 5, complex=True)
u = fes.TrialFunction()
v = fes.TestFunction()

gfu = GridFunction(fes)
fes.ndof